<font size="8">Pull data from Yahoo Finance</font>

In [104]:
import yfinance as yf
import pandas as pd
import numpy as np
import datetime
import plotly.graph_objects as go
import cvxpy as cp

In [105]:
Ticker_names = ['AAPL','MSFT','GOOG','AMZN','TSLA'] # Names of tickers(in yahoo finance) that we want to pull

<font size="6">Get ticker objects</font>

In [106]:
# Create an empty dictionary to store Yahoo Finance Ticker objects
Ticker = dict()

# Iterate through each ticker name in the list Ticker_names
for ticker_name in Ticker_names:
    
    # Create a new entry in the dictionary where the key is the current ticker_name,
    # and the value is a Yahoo Finance Ticker object for the corresponding financial instrument
    Ticker[ticker_name] = yf.Ticker(ticker_name) 
    
# The dictionary Ticker now contains Yahoo Finance Ticker objects for each ticker name
Ticker


{'AAPL': yfinance.Ticker object <AAPL>,
 'MSFT': yfinance.Ticker object <MSFT>,
 'GOOG': yfinance.Ticker object <GOOG>,
 'AMZN': yfinance.Ticker object <AMZN>,
 'TSLA': yfinance.Ticker object <TSLA>}

Pull ticker data by history() method
- interval: data interval (1m data is only for available for last 7 days, and data interval <1d for the last 60 days) Valid intervals are:
“1m”, “2m”, “5m”, “15m”, “30m”, “60m”, “90m”, “1h”, “1d”, “5d”, “1wk”, “1mo”, “3mo”
- start: If not using period – in the format (yyyy-mm-dd) or datetime.
- end: If not using period – in the format (yyyy-mm-dd) or datetime.

In [107]:
# Create an empty dictionary to store historical data for each ticker
Ticker_historical_data = dict()

# Define start and end dates for historical data retrieval
startDate = datetime.datetime(2018, 1, 2)
endDate = datetime.datetime(2021, 12, 31)

# Define the interval for historical data (e.g., daily data)
interval = '1d'

# Iterate through each ticker name in the list Ticker_names
for ticker_name in Ticker_names:
    
    # Retrieve historical data for the current ticker within the specified date range and interval
    historical_data = Ticker[ticker_name].history(start= startDate, end= endDate, interval= interval, prepost= True)[['Close']]
    
    # Rename the 'Close' column to the ticker symbol for clarity
    historical_data.rename(columns={'Close': '%s' % ticker_name}, inplace=True)
    
    # Set the index of the historical data to be the date
    historical_data.index = historical_data.index.date
    
    # Store the historical data for the current ticker in the dictionary
    Ticker_historical_data[ticker_name] = historical_data

# For example, you can access historical data for 'AAPL' using the following:
Ticker_historical_data['AAPL']['AAPL'].tolist()

[40.72287368774414,
 40.715789794921875,
 40.9049072265625,
 41.37062072753906,
 41.216957092285156,
 41.21223068237305,
 41.20277786254883,
 41.436805725097656,
 41.864707946777344,
 41.651947021484375,
 42.33987808227539,
 42.37770080566406,
 42.18859100341797,
 41.84342956542969,
 41.852882385253906,
 41.18622589111328,
 40.45100784301758,
 40.54557418823242,
 39.70634078979492,
 39.4723014831543,
 39.58104705810547,
 39.663795471191406,
 37.94276428222656,
 36.99480056762695,
 38.540870666503906,
 37.7158203125,
 36.67800521850586,
 37.12663269042969,
 38.62204360961914,
 39.00895309448242,
 39.72817611694336,
 41.06218338012695,
 40.92926788330078,
 40.791587829589844,
 40.606441497802734,
 40.94587326049805,
 41.65798568725586,
 42.48164749145508,
 42.34397506713867,
 42.27988815307617,
 41.53929901123047,
 41.826515197753906,
 41.97129821777344,
 41.93569564819336,
 41.54641342163086,
 41.99979019165039,
 42.721378326416016,
 43.13440704345703,
 42.71900177001953,
 42.3558387756

<font size="8">Log Return</font>

\begin{equation}
\text{Log Return} = \ln\left(\frac{S_t}{S_{t-1}}\right)
\end{equation}

Where:
\begin{align*}
\text{Log Return} & \text{ is the logarithmic return of the investment.} \\
S_t & \text{ is the price of the investment at time } t. \\
S_{t-1} & \text{ is the price of the investment at the previous time period, } t-1.
\end{align*}

In [108]:
Price_dataframe = pd.concat(Ticker_historical_data.values(), axis = 1).dropna()

Price_dataframe

AAPL        MSFT        GOOG        AMZN        TSLA
2018-01-02   40.722874   80.229012   53.250000   59.450500   21.368668
2018-01-03   40.715790   80.602371   54.124001   60.209999   21.150000
2018-01-04   40.904907   81.311798   54.320000   60.479500   20.974667
2018-01-05   41.370621   82.319931   55.111500   61.457001   21.105333
2018-01-08   41.216957   82.403915   55.347000   62.343498   22.427334
...                ...         ...         ...         ...         ...
2021-12-23  174.288635  328.668762  147.142502  171.068497  355.666656
2021-12-27  178.292892  336.289154  148.063995  169.669495  364.646667
2021-12-28  177.264618  335.110748  146.447998  170.660995  362.823334
2021-12-29  177.353622  335.798187  146.504501  169.201004  362.063324
2021-12-30  176.186920  333.215454  146.002502  168.644501  356.779999

[1007 rows x 5 columns]

In [109]:
# Create a shifted DataFrame by shifting Price_dataframe by one period
shifting_dataframe = Price_dataframe.shift(periods= 1).T

# Set the first column of the shifted DataFrame to the first row of Price_dataframe
shifting_dataframe[Price_dataframe.index[0]] = Price_dataframe.iloc[0].tolist()

# Create a DataFrame for log returns by taking the natural logarithm of the ratio
# of Price_dataframe to the shifted DataFrame (to calculate daily log returns)
Log_return_dataframe = pd.DataFrame(
                                    np.log(Price_dataframe.values.T / shifting_dataframe.values),
                                    columns= Price_dataframe.index.tolist(),
                                    index= Price_dataframe.columns.tolist()
                                    ).T

# Log_return_dataframe now contains the calculated log returns for each ticker
Log_return_dataframe


AAPL      MSFT      GOOG      AMZN      TSLA
2018-01-02  0.000000  0.000000  0.000000  0.000000  0.000000
2018-01-03 -0.000174  0.004643  0.016280  0.012694 -0.010286
2018-01-04  0.004634  0.008763  0.003615  0.004466 -0.008325
2018-01-05  0.011321  0.012322  0.014466  0.016033  0.006210
2018-01-08 -0.003721  0.001020  0.004264  0.014322  0.060755
...              ...       ...       ...       ...       ...
2021-12-23  0.003637  0.004462  0.001316  0.000184  0.056020
2021-12-27  0.022715  0.022921  0.006243 -0.008212  0.024935
2021-12-28 -0.005784 -0.003510 -0.010974  0.005827 -0.005013
2021-12-29  0.000502  0.002049  0.000386 -0.008592 -0.002097
2021-12-30 -0.006600 -0.007721 -0.003432 -0.003294 -0.014700

[1007 rows x 5 columns]

<font size="8">Mean and Covariance</font>

In [110]:
# Calculate the mean of log returns for each ticker and annualize by multiplying by 30 (assuming 30 trading days in a month)
Mean = np.asarray(np.mean(Log_return_dataframe.values.T, axis= 1)) * 30

# Calculate the covariance matrix of log returns for the tickers and annualize by multiplying by 30
Cov = np.asmatrix(np.cov(Log_return_dataframe.values.T)) * 30

print('Mean array is',Mean)
print('Covariance matrix is',Cov)

Mean array is [0.04363721 0.04242018 0.03004844 0.03106203 0.08386873]
Covariance matrix is [[0.01289868 0.00888883 0.00772452 0.00791077 0.01083714]
 [0.00888883 0.01061028 0.00821058 0.00790703 0.01024045]
 [0.00772452 0.00821058 0.01014058 0.00727249 0.00842211]
 [0.00791077 0.00790703 0.00727249 0.0115663  0.00927403]
 [0.01083714 0.01024045 0.00842211 0.00927403 0.05010398]]


<font size="8">Mean-Variance Criteria</font>

The optimal portfolio $x$ is a vector of weights which yields the minimum portfolio return variance subject to required return constraint and the cost constraint. Mathematically, the problem is the find the solution of

$$\begin{aligned}
	        \min_X \quad         & X^\top\Sigma X,\\
	        \textrm{subject to} \quad   & X^\top\boldsymbol{\mu}\geq r,\\
	        \textrm{and} \quad          & X^\top1=1.
	\end{aligned}$$

In [111]:
#create the decision variable x with lenth equals the length of mu
X = cp.Variable(len(Mean))
#define the required return (3 percent per month in this example)
r = 0.03

#define the objective function
Portfolio_Risk = cp.quad_form(X,Cov)
Objective = cp.Minimize(Portfolio_Risk)

#define constraints
Portfolio_Return = X.T@Mean
Constraints = [Portfolio_Return >= r,sum(X)==1]

#solve the optimization problem
problem = cp.Problem(Objective, Constraints)
problem.solve()

#extract the optimal portfolio
optimal_Portfolio = X.value

<font size="8">Optimal portfolio</font>

In [112]:
print('The optimal portfolio proportion is ', dict(zip(Ticker_names,optimal_Portfolio)))
print('The mean of return is %f' % np.mean(Portfolio_Return.value))
print('The variance of the portfolio return is %f'%Portfolio_Risk.value)

The optimal portfolio proportion is  {'AAPL': 0.13562283096959474, 'MSFT': 0.19689843193423415, 'GOOG': 0.40332117236333115, 'AMZN': 0.2807261221003196, 'TSLA': -0.016568557367479687}
The mean of return is 0.033720
The variance of the portfolio return is 0.008656


In [113]:
#plot the optimal portfolio
hist = go.Figure(go.Bar(x= Ticker_names,
    y=optimal_Portfolio,text=np.round(optimal_Portfolio,decimals=2),textposition='auto'))

hist.update_layout(xaxis_title = 'Asset', yaxis_title = 'Proportion', title = 'Portfolio Proportion')
hist.show()


In [114]:
#display portfolio return and risk
Portfolio_Risk_Base = Portfolio_Risk.value
print(Portfolio_Return.value)
print(Portfolio_Risk.value)

0.03372018081156824
0.0086562174985223


# STEP 6: Simulation of the future returns of the assets and the portfolio

Please note that we assume that the vector of the log returns of the assets is normally distributed with mean $\mu$ and covariance $\Sigma$. Calculating the future return of the optimal portfolio can be done by

1. Simulate $m$ scenarios of the vector of the log returns from the normal distribution with mean $\mu$ and covariance $\Sigma$.
2. Calculate the portfolio return of the optimal portfolio by multiplying the simulated vector of the log return to the vector of the optimal weights.

In [ ]:
def Multivariate_simulation(scenario, Mean, Cov):
    """Simulate the expected return of each asset.

    Args:
        scenario (int): Number of scenarios to simulate.
        Mean (1-D array): Mean list.
        Cov (n-D array): Covariance matrix.

    Returns:
        n-D array: Matrix of scenarios of the expected return of each asset.
    """    
    number_of_assets = len(Mean)
    
    # Generate random samples from a multivariate normal distribution
    mean_simulation = np.random.multivariate_normal(np.zeros(number_of_assets), Cov, size=scenario)
    
    # Shift the simulated values by the mean to obtain scenarios of expected returns
    return mean_simulation + Mean


In [115]:
def multivariate_t_rvs(m, S, df=np.inf, n=100000):
    '''generate random variables of multivariate t distribution
    Parameters
    ----------
    m : array_like
        mean of random variable, length determines dimension of random variable
    S : array_like
        square array of covariance  matrix
    df : int or float
        degrees of freedom
    n : int
        number of observations, return random array will be (n, len(m))
    Returns
    -------
    rvs : ndarray, (n, len(m))
        each row is an independent draw of a multivariate t distributed
        random variable
    '''
    m = np.asarray(m)
    d = len(m)
    if df == np.inf:
        x = np.ones(n)
    else:
        x = np.random.chisquare(df, n) / df
    z = np.random.multivariate_normal(np.zeros(d), S, (n,))
    return m + z/np.sqrt(x)[:,None]   # same output format as random.multivariate_normal

#simulate 100,000 scenarios of the vector of the log returns of the assets.
Simulated_Return = Multivariate_simulation(scenario = 100000, Mean = Mean, Cov = Cov)
#calculate the portfolio return based on the simulated returns.
Simulated_Portfolio_Return = [np.dot(optimal_Portfolio,Simulated_Return[i]) for i in range(len(Simulated_Return))]

In [116]:
# Specify the bin size for the histogram
size = 0.01

# Create a histogram using Plotly (go.Histogram) for the optimal portfolio payoffs
hist = go.Figure(data=[go.Histogram(x=Simulated_Portfolio_Return, xbins=dict(
    start=min(Simulated_Portfolio_Return) // size * size,  
    end=max(Simulated_Portfolio_Return) // size * size + size,  
    size=size
))])

# Update layout settings for the histogram
hist.update_layout(
    title_text='Histogram of the portfoilo return based on 100,000 simulations',  # title of plot
    xaxis_title_text='Portfolio Return',  # x-axis label
    yaxis_title_text='Count',  # y-axis label
    bargroupgap=0.1  # gap between bars of the same location coordinates
)

hist.show()


<font size="8">Comparison of the portfolios  obtained with two different required returns</font>

In [117]:
def Mean_Variance_optimization(return_array, covariance_matrix, require_return, short_sell=None):
    """
    Optimize the portfolio for mean-variance using convex optimization.

    Args:
        return_array (array): Array of expected returns for each asset.
        covariance_matrix (array): Covariance matrix of asset returns.
        require_return (float): Required return for the portfolio.
        short_sell (str, optional): If short selling is allowed, input 'yes'. Defaults to None.

    Returns:
        tuple: Portfolio weights, objective value, and portfolio return.
    """    
    # Define the decision variable for portfolio weights
    X = cp.Variable(len(return_array))
    
    # Formulate the objective function as the quadratic form of portfolio weights and covariance matrix
    objective_formulation = cp.quad_form(X, covariance_matrix)
    
    # Define the objective function to minimize the variance
    objective_function = cp.Minimize(objective_formulation)
    
    # Calculate the expected return of the portfolio
    Return = return_array.T @ X
    
    # Define constraints based on the specified conditions (short selling or not)
    if short_sell == None:
        
        constraints = [sum(X) == 1, Return >= require_return, X >= 0]
    else:
        
        constraints = [sum(X) == 1, Return >= require_return]
    
    # Formulate the convex optimization problem
    problem = cp.Problem(objective_function, constraints)
    
    # Solve the optimization problem
    problem.solve()
    
    if problem.status != 'optimal':
        
        optimal_portfolio = np.array([0 for i in range(len(return_array))])
    
    else:
        
        optimal_portfolio = X.value
        
    # Return the optimized portfolio weights, objective value (variance), and the expected return of the portfolio
    return optimal_portfolio, problem.value, Return.value


In [118]:
require_return_2 = 0.08
optimal_Portfolio2,__,__ = Mean_Variance_optimization(Mean, Cov, require_return_2, short_sell='yes')

In [119]:
#plot the optimal portfolio
hist = go.Figure(go.Bar(x= Ticker_names,
    y=optimal_Portfolio,text=np.round(optimal_Portfolio2,decimals=2),textposition='auto'))

hist.update_layout(xaxis_title = 'Asset', yaxis_title = 'Proportion', title = 'Portfolio Proportion')
hist.show()


In [120]:
#simulate 100,000 scenarios of the vector of the log returns of the assets.
Simulated_Return_2 = multivariate_t_rvs(Mean, Cov, df=np.inf, n=100000)
#calculate the portfolio return based on the simulated returns.
Simulated_Portfolio_Return_2 = [np.dot(optimal_Portfolio2,Simulated_Return_2[i]) for i in range(len(Simulated_Return_2))]

In [121]:
# Specify the bin size for the histogram
size = 0.01

# Create a histogram using Plotly (go.Histogram) for the optimal portfolio payoffs
hist = go.Figure(data=[go.Histogram(x=Simulated_Portfolio_Return, xbins=dict(
    start=min(Simulated_Portfolio_Return) // size * size,  
    end=max(Simulated_Portfolio_Return) // size * size + size,  
    size=size
), name='Require Return is %.2f' % 0.01)])

# Update layout settings for the histogram
hist.update_layout(
    title_text='Histogram of the portfoilo return based on 100,000 simulations',  # title of plot
    xaxis_title_text='Portfolio Return',  # x-axis label
    yaxis_title_text='Count',  # y-axis label
    bargroupgap=0.1  # gap between bars of the same location coordinates
)

# Add a histogram for the random portfolio payoffs
hist.add_trace(go.Histogram(x=Simulated_Portfolio_Return_2, xbins=dict(
    start=min(Simulated_Portfolio_Return_2) // size * size,  # type: ignore
    end=max(Simulated_Portfolio_Return_2) // size * size + size,  # type: ignore
    size=size
), name='Require Return is %.2f' % require_return_2))

# The two histograms are drawn on top of one another
hist.update_layout(barmode='overlay')
hist.update_traces(opacity=0.5)


hist.show()


<font size="8">Efficient frontier</font>

The efficient frontier is a plot between the required returns and the minimum SDs obtained with optimal portfolio. The compuatation steps are

1. Determine the range of required returns you want to plot the efficient frontier for.
2. For each required return, perform the optimization to find the optimal portfolio.
3. Find the minimum SD coresponding with the optimal portfolio.
4. Plot between the minimum SDs and the required returns.

In [126]:
require_return_list = [0.01*i for i in range(30)]
Return = dict()
Risk = dict()

for i in require_return_list:
    
    __,Risk[i],Return[i] = Mean_Variance_optimization(Mean, Cov, i, short_sell='yes')
    
Efficient_Frontier_Table = pd.DataFrame({'Require Return':list(Return.values()),
                                         'Risk':list(Risk.values())})

In [127]:
Efficient_Frontier_Table

Require Return      Risk
0          0.03372  0.008656
1          0.03372  0.008656
2          0.03372  0.008656
3          0.03372  0.008656
4          0.04000  0.009066
5          0.05000  0.011413
6          0.06000  0.015840
7          0.07000  0.022347
8          0.08000  0.030934
9          0.09000  0.041601
10         0.10000  0.054349
11         0.11000  0.069177
12         0.12000  0.086086
13         0.13000  0.105074
14         0.14000  0.126143
15         0.15000  0.149292
16         0.16000  0.174521
17         0.17000  0.201831
18         0.18000  0.231221
19         0.19000  0.262691
20         0.20000  0.296241
21         0.21000  0.331872
22         0.22000  0.369583
23         0.23000  0.409374
24         0.24000  0.451245
25         0.25000  0.495197
26         0.26000  0.541229
27         0.27000  0.589341
28         0.28000  0.639534
29         0.29000  0.691806

In [129]:
fig = go.Figure(data=go.Scatter(x=list(Risk.values()), y=list(Return.values()),name='The efficient frontier'))

fig.update_layout(
    title_text='The efficient frontier', # title of plot
    xaxis_title_text='Risk(Mean-Variance)', # xaxis label
    yaxis_title_text='Return', # yaxis label
    # bargap=0.2, # gap between bars of adjacent location coordinates
    bargroupgap=0.1 # gap between bars of the same location coordinates
)